In [1]:
import numpy as np
import math
import os.path as osp
import mediapy as media
import numpy as np
import matplotlib.pyplot as plt
import json
from typing import List, Optional
import utils

In [2]:
# @title utils
def load_rgbd_cam_from_pkl(vid: str, root_dir: str, npz_folder: str, hfov: float, new_imw=1, new_imh=1):
  """load rgb, and camera"""
  input_dict = {'left': {'camera': [], 'video': []}}
  # Load camera
  dp = utils.load_dataset_npz(osp.join(npz_folder, f'{vid}.npz'))
  extrs_rectified = dp['extrs_rectified']

  nfr = len(extrs_rectified)
  input_dict['nfr'] = nfr
  for fid in range(nfr):
    intr_normalized = {
        'fx': (1 / 2.0) / math.tan(math.radians(hfov / 2.0)),
        'fy': (
            (1 / 2.0) / math.tan(math.radians(hfov / 2.0)) * new_imw / new_imh
        ),
        'cx': 0.5,
        'cy': 0.5,
        'k1': 0,
        'k2': 0,
    }
    input_dict['left']['camera'].append(
        utils.CameraAZ(
            from_json={
                'extr': extrs_rectified[fid][:3, :],
                'intr_normalized': intr_normalized,
            }
        )
    )
  video_path = osp.join(
      root_dir,
      vid,
      vid + '-left_rectified.mp4',
  )
  rgbs = media.read_video(video_path)
  input_dict['left']['video'] = rgbs
  return input_dict

In [5]:
# @title define input
vid = 'CMwZrkhQ0ck_130030030'
npz_folder = 'stereo4d_dataset/npz'
root_dir = 'stereo4d_dataset/processed'
hfov = 60
dp = utils.load_dataset_npz(osp.join(npz_folder, f'{vid}.npz'))

input_dict = load_rgbd_cam_from_pkl(vid, root_dir, npz_folder, hfov)
track3d = utils.Track3d(
  track3d=dp['track3d'],
  visible_list=~np.isnan(dp['track3d']).any(axis=-1),
  video=input_dict['left']['video'],
  cameras=input_dict['left']['camera']
)
print("track shape:", track3d.track3d.shape)

track shape: (88782, 199, 3)


In [6]:
# @title visualize 512 tracks projected onto video frames.
track_vis = utils.plot_3d_tracks_plt(
  input_dict['left']['video'],
  track3d.get_new_track(percentage=min(512 / len(track3d.track3d), 1)),
)
media.show_video(track_vis, fps=30)

This browser does not support the video tag.
